Можем ли мы использовать классификацию изображений для решения задачи поиска похожих изображений? И возможно ли обучить для этой задачи довольно надежную, глубокую CNN? Причем ее результат должен быть стабильным при разных ракурсах, освещении, позе, и.т.д.

![](https://courses.cv-gml.ru/storage/seminars/metric-learning/img1.png)

Обычно это достигается, когда у нас есть хороший объем данных. Например, $1000$ примеров для каждого класса. В классификации изображений, если количество точек данных в классе невелико, это может привести к переобучению и очень плохим результатам. Кроме того, классификация изображений обычно хорошо работает, когда количество классов невелико.

Однако, как правило, это не относится к задачам проверки личности / изображения. Тут все совсем наоборот. Здесь у нас обычно очень большое количество классов, а количество примеров на класс довольно мало. И здесь на помощь приходит few-shot/one-shot learning.


### Few-shot Learning
Это задача классификации, цель которой - научиться отличать классы объектов по одному / нескольким обучающим примерам. Например, в задаче распознавания лиц по одному примеру человека нужно научиться его узнать.

Модели глубокого обучения не будут работать с одним учебным примером. Как решить эту проблему? Вместо решения исходной задачи будем обучать **функцию "похожести"** разных примеров. То есть **метрику** для их сравнения.


### Простая модель
Сначала попробуем обучить простую модель для классификации людей по лицам. И будем использовать выходы предпоследнего слоя для обучения метода ближайших соседей и нахождения похожих людей.

In [ ]:
import os
import random

import albumentations as A
import albumentations.pytorch
import lightning as L
import matplotlib.pyplot as plt
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchmetrics
import torchvision
from PIL import Image
from sklearn.neighbors import KNeighborsClassifier
from torch.utils import data
from torchvision.utils import make_grid

# Increase these if figures appear small
plt.rcParams["figure.figsize"] = fx, fy = (14.08, 6.40)

# Not using `bfloat16` matrix multiplication for consistency
# You might get better performance without much precision loss
# by setting this to "medium" on some devices
torch.set_float32_matmul_precision("high")

In [ ]:
if torch.cuda.is_available():
    DEVICE = torch.device("cuda")
    print("Using the GPU 😊")
else:
    DEVICE = torch.device("cpu")
    print("Using the CPU 😞")

In [ ]:
if not os.path.exists("lfw"):
    !curl -O https://courses.cv-gml.ru/storage/seminars/metric-learning/lfw.tgz
    !tar -xf lfw.tgz

In [ ]:
MAX_EPOCHS = 5
BATCH_SIZE = 64
EMB_DIM = 512

Напишем датапровайдер. При этом в нем будет функция `make_slice`, которая в зависимости от параметра `leave` либо только оставляет, либо наоборот убирает индексы из списка `base_elems`.

Мы будем использовать набор даных [`LFW`](http://vis-www.cs.umass.edu/lfw/). Сам по себе этот набор, как правило, используется только как бенчмарк, а не для обучения полноценных моделей. Однако реальные датасеты для обучения (например, [`CelebA`](http://mmlab.ie.cuhk.edu.hk/projects/CelebA.html) имеют очень большой размер и они слишком большие для данного семинара. Однако из-за того, что мы используем плохой датасет (и плохую модель), получаемое качество моделей будет не очень хорошим.

In [ ]:
def split_by_index(elems, index):
    targets = [], []
    for i, elem in enumerate(elems):
        targets[i in index].append(elem)
    return targets


class LFWDataset(torch.utils.data.Dataset):
    def __init__(self, folder, people_list, transforms):
        super().__init__()
        self.people_list = people_list
        self.need_classes = [i for i in range(len(people_list))]
        self.images = []
        self.labels = []
        self.weights = []
        self.class_to_idxs = {}
        for i, person in enumerate(people_list):
            self.class_to_idxs[i] = []
            fnames = sorted(os.listdir(os.path.join(folder, person)))
            for fname in fnames:
                image = Image.open(os.path.join(folder, person, fname))
                image = np.asarray(image.convert("RGB"))
                self.images += [image]
                self.labels += [i]
                self.weights += [1.0 / len(fnames)]
                self.class_to_idxs[i].append(len(self.images) - 1)
        self.transform = transforms

    def __getitem__(self, index):
        target = self.labels[index]
        sample = self.transform(image=self.images[index])["image"]
        return sample, target

    def __len__(self):
        return len(self.labels)

    def make_slice(self, base_elems, leave=True):
        self.images = split_by_index(self.images, base_elems)[leave]
        self.weights = split_by_index(self.weights, base_elems)[leave]
        self.labels = split_by_index(self.labels, base_elems)[leave]

        self.class_to_idxs = {i: [] for i in range(len(self.people_list))}
        for idx, label in enumerate(self.labels):
            self.class_to_idxs[label].append(idx)

Построим списки людей для обучения и тестирования.

In [ ]:
train_people = []
test_people = []
for person in sorted(os.listdir("lfw")):
    cnt = len(os.listdir("lfw/" + person))
    if cnt >= 3:
        train_people.append(person)
    elif cnt >= 2:
        test_people.append(person)

Зададим аументацию данных. Сделаем три набора данных:
- train_data - обучающая выборка - все картинки, встречающиеся хотя бы 3 раза
- test_data_index - фото по одному кадру людей из тестовой выборки (не лежащие в ней) (одно из двух фото)
- test_data - фото кадров людей из тестовой выборки (одно из двух фото)

Построим для этих наборов `DataLoader`-ы.

In [ ]:
train_transform = A.Compose(
    [
        A.HorizontalFlip(0.5),
        A.Rotate(15),
        A.RandomResizedCrop((224, 224), scale=(0.6, 1.0)),
        A.RGBShift(r_shift_limit=10, g_shift_limit=10, b_shift_limit=10, p=0.5),
        A.RandomBrightnessContrast(0.1, 0.1, p=0.5),
        A.Normalize(mean=(0.485, 0.456, 0.406), std=(0.229, 0.224, 0.225)),
        A.pytorch.ToTensorV2(),
    ],
)

test_transform = A.Compose(
    [
        A.Resize(224, 224),
        A.Normalize(mean=(0.485, 0.456, 0.406), std=(0.229, 0.224, 0.225)),
        A.pytorch.ToTensorV2(),
    ],
)

In [ ]:
train_data = LFWDataset("lfw", train_people, train_transform)
test_data_index = LFWDataset("lfw", test_people, test_transform)
test_data = LFWDataset("lfw", test_people, test_transform)

random.seed(51)
base_elems = []
for clas, idxs in test_data_index.class_to_idxs.items():
    idx = random.choice(idxs)
    base_elems.append(idx)
test_data_index.make_slice(base_elems, True)
test_data.make_slice(base_elems, False)

sampler = data.WeightedRandomSampler(
    train_data.weights,
    len(train_data.weights),
)
train_dl = data.DataLoader(
    train_data,
    BATCH_SIZE,
    sampler=sampler,
    num_workers=4,
    pin_memory=True,
)
oneshot_dl = data.DataLoader(
    test_data_index,
    BATCH_SIZE,
    num_workers=4,
    pin_memory=True,
)
test_dl = data.DataLoader(
    test_data,
    BATCH_SIZE,
    num_workers=4,
    pin_memory=True,
)

Визуализируем получающиеся у нас данные.

In [ ]:
def show_batch(dl):
    for batch in dl:
        images, labels = batch
        fig, ax = plt.subplots(figsize=(7.5, 7.5))
        ax.set_yticks([])
        ax.set_xticks([])
        sample = images[:20]
        sample = sample - sample.min()
        sample = sample / sample.max()
        ax.imshow(make_grid(sample, nrow=5).permute(1, 2, 0))
        break

In [ ]:
show_batch(train_dl)
show_batch(test_dl)

In [ ]:
class BaseEmbeddingTrainer(L.LightningModule):
    def __init__(self, *, emb_net, **kwargs):
        super().__init__(**kwargs)
        self.emb_net = emb_net

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=1e-3)

    def _log_metrics(self, loss, accs, kind):
        metrics = {}
        if loss is not None:
            metrics[f"{kind}_loss"] = loss
        if accs is not None:
            metrics[f"{kind}_accs"] = accs
        self.log_dict(
            metrics,
            prog_bar=True,
            logger=True,
            on_step=kind == "train",
            on_epoch=True,
        )
        return loss

Зададим модель `EmbeddingNet` для извлечения признаков изображений людей.

In [ ]:
class EmbeddingNet(nn.Sequential):
    def __init__(self):
        super().__init__()

        ### YOUR CODE HERE
        self.convnet = ...
        self.convnet.fc = ...

Зададим модель `ClassificationTrainer` для построения классификатора людей где на каждого человека отведен свой класс.

In [ ]:
class ClassificationTrainer(BaseEmbeddingTrainer):
    def __init__(self, *, train_classes, **kwargs):
        super().__init__(**kwargs)
        self.accuracy = torchmetrics.Accuracy(
            task="multiclass",
            num_classes=train_classes,
        )

        ### YOUR CODE HERE
        self.classifier = ...

    def training_step(self, batch):
        x, y = batch

        f = self.emb_net(x)
        p = self.classifier(f)

        loss = F.cross_entropy(p, y)
        accs = self.accuracy(p.argmax(dim=-1), y)

        return self._log_metrics(loss, accs, "train")

Обучим модель

In [ ]:
def train_model(
    model,
    experiment_path,
    train_dl,
    max_epochs=MAX_EPOCHS,
    **trainer_kwargs,
):
    callbacks = [
        L.pytorch.callbacks.TQDMProgressBar(leave=True),
        L.pytorch.callbacks.LearningRateMonitor(),
    ]
    trainer = L.Trainer(
        callbacks=callbacks,
        max_epochs=max_epochs,
        default_root_dir=experiment_path,
        **trainer_kwargs,
    )
    trainer.fit(model, train_dl)
    return model

In [ ]:
net = train_model(
    ClassificationTrainer(
        emb_net=EmbeddingNet(),
        train_classes=len(train_data.people_list),
    ),
    "runs/train_cls",
    train_dl,
)

Обучим k-NN на изображениях из идекса людей. Протестируем ее на наборе из тех же людей, но других их изображениях.

In [ ]:
def run_emb_net(emb_net, dataloader, normalize=False):
    ### YOUR CODE HERE
    ...

In [ ]:
def train_knn(emb_net, normalize=False):
    ### YOUR CODE HERE
    ...

In [ ]:
def test_knn(emb_net, knn, normalize=False):
    ### YOUR CODE HERE
    ...

In [ ]:
net.eval()
net.emb_net.to(DEVICE)
knn = train_knn(net.emb_net)
test_knn(net.emb_net, knn)

### Метрика:
Метрика - это неотрицательная функция $d (x, y)$ между двумя точками $x$ и $y$, которая описывает так называемое понятие "расстояния" между этими двумя точками. Формально, есть несколько свойств, которым должна удовлетворять метрика:
- Неотрицательность: $d (x, y) ≥ 0$ и $d (x, y) = 0$, если $x = y$.
- Ннеравенство треугоьлника: $d (x, y) ≤ d (x, z) + d (z, y)$.
- Симметричность: $g (x, y) = g (y, x)$.

### Примеры:
- Евклидова метрика: в d-мерном векторном пространстве
$$d(x, y) = \sqrt{\sum_{i=1}^d (x_i-y_i)^2}$$
- Дискретная метрика:
$$\begin{cases}
    1, x \neq y\\
    0, x == y
\end{cases} 
$$

### Обучение метрик:

Что делает базовый алгоритм машинного обучения? - Учитывая данные и соответствующие выходные метки, настраивается набор правил или некоторая сложная функция, которая входным данным сопоставляет соответствующие выходные метки.

Одним из простейших алгоритмов машинного обучения, в котором фиксируется информация о расстоянии, является алгоритм $kNN$, идея которого состоит в том, чтобы найти окрестность $k$ ближайших точек данных для новой точки. Далее этой точке назначается класс, которому принадлежит большинство из $k$ точек окрестности.

![](https://courses.cv-gml.ru/storage/seminars/metric-learning/img2.png)

У метрического обучения похожая цель - изучить функцию похожести на основе данных. Метрическое обучение направлено на изучение встраиваемых данных / векторов признаков таким образом, чтобы уменьшить расстояние между векторами признаков, соответствующими примерам, принадлежащим одному классу, и увеличить расстояние между векторами признаков, соответствующими разным классам.

Евклидовы расстояния менее значимы в больших измерениях. Им не удается уловить нелинейность данных по ряду причин:
- Они представляют собой изотропную (одинаковую во всех направлениях) метрику расстояния.
- Эти расстояния не отражают структуру классов.

Можно использовать неизотропные расстояния, которые используют свойства данных для определения структуры отношений классов. Расстояние Махаланобиса - одна из таких метрик:

$$d(x, y) = \sqrt{(x-y)^TM(x-y)}$$

Здесь $M$ является обратной матрицей ковариации и действует как весовой член квадрата евклидова расстояния. 


### Deep metric learning
Deep metric learning использует нейронные сети для автоматического изучения отличительных характеристик изображений и вычисления метрики их похожести.

Зачем нужно глубокое метрическое обучение?
- Нужна устойчивость моделей при смене позы/ракурса/освещения.
- Это прикладная задача. Например, создание эффективной системы проверки лиц. При этом не хочется обучать её полностью с нуля с каждым новым примером в системе.
- Классическое Metric Learning имеет лишь ограниченную возможность фиксировать нелинейность данных.
- Глубокое метрическое обучение помогает фиксировать нелинейную структуру данных.

Далее рассмотрим функции потерь для обучения таких нейронных сетей.


### Siamese Networks:

Одна из фундаментальных идей - это сиамская нейросетевая модель. Сиамская сеть - это архитектура симметричной нейронной сети, состоящая из двух идентичных подсетей, которые используют одни и те же наборы параметров и обучаются, вычисляя метрику между по последним слоям каждой подсети.

![](https://courses.cv-gml.ru/storage/seminars/metric-learning/img3.png)

Обозначим преобразование, выполняемое нейросетью, как $f(x)$, а расстояние между примерами $d (f(x), f(y))$. Наша цель состоит в следующем:

- Если $x$ и $y$ - примеры одного и того же класса, то $d (f(x), f(y))$ мало,
- Если $x$ и $y$ - примеры разных классов $d (f(x), f(y))$ большое.

Сиамские сети часто используются в сочетании с **Contrastive loss**.


Зададим класс `SiameseTrainer` для обучения сиамских сетей.

In [ ]:
class SiameseTrainer(BaseEmbeddingTrainer):
    def __init__(self, *, loss_functor, **kwargs):
        super().__init__(**kwargs)
        self.loss_functor = loss_functor

    def training_step(self, batch):
        xs, ys = batch

        ### YOUR CODE HERE
        fs = ...
        loss = ...

        return self._log_metrics(loss, None, "train")

### Contrastive loss:
Эта loss-функция обучает вектора признаков таким образом, чтобы расстояние между двумя примерами из одного и того же класса было небольшим, а расстояние между разными классами было большим. А теперь давайте разберемся с математикой:
$$L=L(f(x), f(y), z) = z ||f(x) - f(y)||_2^2 + (1-z)max\{0, m - ||f(x) - f(y)||_2\}^2$$

Здесь $m> 0$ - отступ, $z$ - логическое значение, равное 1, если $x$, $y$ - примеры одного класса, и $0$ в противном случае, $||*||_2$ - норма $L_2$.

Давайте разберемся в этом уравнении. Если $x$ и $y$ являются парами одного класса и $z$ равно $1$, то второй член исчезает ($m$ не влияет). И функция минимизирует первое слагаемое - расстояние между примерами одного класса.

Теперь, если $x$ и $y$ - это пары разного класса и $z$ равно $0$, то первый член равен нулю. Если сеть считает, что $x$ и $y$ похожи, а расстояние между ними невелико, то мы получим значение loss-функции, близкое к $m$.

Роль отступа $m$: Следует отметить, пары разных классов дадут вклад в функцию потерь только в том случае, если расстояние $||f(x) - f(y)||_2^2 < m$. Это означает, что функцию не будет заботить, как далеко отойдут отрицательные пары $x$ и $y$, когда этот предел $m$ достигнет. Таким образом, он может больше сосредоточиться на трудных точках.


Зададим класс `ContrastiveLFW`, который будет предоставлять данные для обучения сиамской сети. Он будет для данного изображения дополнительно генерировать с вероятностью `0.5` либо другой пример того же класса, либо пример другого класса.

In [ ]:
def random_choice_except(options, exception):
    ### YOUR CODE HERE
    ...

In [ ]:
class ContrastiveLFW(torch.utils.data.Dataset):
    def __init__(self, lfw_dataset):
        super().__init__()
        self.lfw_dataset = lfw_dataset

    def __getitem__(self, index):
        ### YOUR CODE HERE
        sample1, target1 = ...
        sample2, target2 = ...

        return [sample1, sample2], [target1, target2]

    def __len__(self):
        return len(self.lfw_dataset)

Зададим провайдеры данных.

In [ ]:
train_siamese_data = ContrastiveLFW(train_data)
contr_train_dl = data.DataLoader(
    train_siamese_data,
    BATCH_SIZE,
    num_workers=4,
    pin_memory=True,
    shuffle=True,
)

Реализуем loss-функцию.

In [ ]:
class ContrastiveLoss(nn.Module):
    def __init__(self, margin):
        super().__init__()
        self.margin = margin
        self.eps = 1e-9

    def forward(self, fs, ys):
        f1, f2 = fs
        y1, y2 = ys

        m = self.margin
        eps = self.eps

        ### YOUR CODE HERE
        ...

Обучим сеть.

In [ ]:
net_contr = train_model(
    SiameseTrainer(
        emb_net=EmbeddingNet(),
        loss_functor=ContrastiveLoss(margin=2.0),
    ),
    "runs/siamese_contrastive",
    contr_train_dl,
)

Протестируем качество k-NN.

In [ ]:
net_contr.eval()
net_contr.emb_net.to(DEVICE)
knn = train_knn(net_contr.emb_net)
test_knn(net_contr.emb_net, knn)

### Triplet loss

Триплетная сеть состоит из трех идентичных подсетей, которые имеют одинаковые наборы параметров. Обучение выполняется в виде набора из трех изображений: 1) Якорное изображение (базовое изображение), 2) Позитивное изображение (принадлежащее к тому же классу, что и якорь), 3) Негативное изображение (изображение, не принадлежащее классу якоря).

![](https://courses.cv-gml.ru/storage/seminars/metric-learning/img4.png)

Цель triplet loss - гарантировать, что якорное изображение близко ко всем изображениям того же класса. Отрицательных примеры должны быть дальше, чем положительные.

$$L=L(f(A), f(B), f(C)) = max\{0, ||f(A) - f(B)||_2^2 - ||f(A) - f(C)||_2^2 + m\}$$
В этой формуле $A$ - якорь, $B$ - позитивный пример, $C$ - негативный пример, $m$ - параметр, $||*||_2$ - норма $L_2$.

Давайте разберемся в этом уравнении. Когда loss-функция будет равна $0$? Второй член внутри $max(*)$ должен быть $<=0$, то есть $d(A, N) >= d(A, B) + m$. Если это произойдет, то на этой тройке параметры нейросети при обучении не обновятся.

Когда loss-функция будет положительна? Когда, $d (A, N) < d (A, B) + m$. Полезными и трудными для обучения являются тройки, в которых $d (A, N) << d (A, B)$.


Зададим класс `TripletLFW`, который будет предоставлять данные для обучения сиамской сети. Он будет для данного изображения дополнительно генерировать положительный пример того же класса и отрицательный пример другого класса.

In [ ]:
class TripletLFW(torch.utils.data.Dataset):
    def __init__(self, lfw_dataset):
        super().__init__()
        self.lfw_dataset = lfw_dataset

    def __getitem__(self, index):
        ### YOUR CODE HERE
        sample1, target1 = ...
        sample2, target2 = ...
        sample3, target3 = ...

        return [sample1, sample2, sample3], [target1, target2, target3]

    def __len__(self):
        return len(self.lfw_dataset)

Зададим провайдеры данных.

In [ ]:
train_triplet_data = TripletLFW(train_data)
triplet_train_dl = data.DataLoader(
    train_triplet_data,
    BATCH_SIZE,
    num_workers=4,
    pin_memory=True,
    shuffle=True,
)

Реализуем loss-функцию.

In [ ]:
class TripletLoss(nn.Module):
    def __init__(self, margin):
        super().__init__()
        self.margin = margin

    def forward(self, fs, ys):
        del ys
        anchor, positive, negative = fs
        m = self.margin

        ### YOUR CODE HERE
        ...

Обучим сеть.

In [ ]:
net_triplet = train_model(
    SiameseTrainer(
        emb_net=EmbeddingNet(),
        loss_functor=TripletLoss(margin=2.0),
    ),
    "runs/siamese_triplet",
    triplet_train_dl,
)

Протестируем качество k-NN.

In [ ]:
net_triplet.eval()
net_triplet.emb_net.to(DEVICE)
knn = train_knn(net_triplet.emb_net)
test_knn(net_triplet.emb_net, knn)

### ArcFace loss
Данная функция потерь для обучения метрик основана на другой идее. Тут предлагается сравнивать расстояния не по $L_2$ метрике, а по углу до вектора, представляющего нужный класс.

Обычная `Softmax`-функция потерь имеет вид:
$$L = -\frac{1}{M}\sum_{i=1}^M log(\frac{e^{W^T_{y_i} f_i}}{\sum_{k=1}^C e^{W^T_{k} f_i}})$$
Где $f_i$ - это вектор-признаки, подающиеся на последний полносвязный слой, а $W$ - матрица весов линейного преобразования этого слоя.

Рассмотрим задачу классификации на два класса, обученную с использованием функции потерь softmax. Пусть $w_1$ и $w_2$ - векторы для классификации на классы 1 и 2 соответственно. Предположим, что **bias=0**. Точка данных $x_i$ прогнозируется как класс 1, если для вектора признаков $f_i$ выполнено (ниже скалярные произведения):
$$||w_1|| * ||f_i|| * cos(\theta_1) > ||w_2|| * ||f_i|| * cos(\theta_2)$$
Предположим, что $||w_1||=||w_2||=1$, тогда выражение сверху эквивалентно:
$$cos(\theta_1) > cos(\theta_2)$$
То есть на самом деле нам интересен только угол до ближайшего вектора, представляющего класс.

![](https://courses.cv-gml.ru/storage/seminars/metric-learning/img5.png)

Чтобы правильно обучить такие признаки, норма $W$ обязательно должна быть одинакова для всех классов, $||w_i|| = 1$, $bias=0$. На этапе обучения мы фиксируем $||f|| = s$ ($s$ называется "параметр масштабирования"). Так удаляются вариации в радиальных направлениях и разделение происходит только в угловом пространстве на гиперсфере с радиусом s.

На этапе тестирования оценка схожести пары лиц рассчитывается в соответствии с косинусным сходством между двумя векторами признаков. При этом косинус угла между векторами $x$ и $y$ равен $\theta_{x,y}=\frac{x^Ty}{||x||*||y||}$, а евклидово расстояние $||x-y|| = sqrt(x^Tx+y^Ty-2*x^Ty)$. Если положит $||x||=||y||=1$, то $\theta_{x,y}=x^Ty$, а $||x-y|| = sqrt(2-2*x^Ty)$.  Когда косинус растет, Евклидово расстояние уменьшается, и наоборот. Поэтому можно продолжать использовать евклидово расстояние в $k-NN$, только надо не забыть нормировать векторы.

Основанная на этих идеях функция потерь *ArcFace loss* имеет вид:

$$L_{arcface} = -\frac{1}{M}\sum_{i=1}^M log(\frac{e^{s*cos(\theta_{y_i, i}+m)}}{e^{s*cos(\theta_{y_i, i}+m)} + \sum_{k \neq y_i}^C e^{s*cos(\theta_{k, i})}})$$

Она минимизируется, когда $cos(\theta_{y_i, i}+m) > cos(\theta_{k, i})$ при $k \neq y_i$. Это означает, что $\theta_{y_i, i}+m < \theta_{k, i}$, то есть угол до $y_i$-го класса меньше, чем до другого $k$-го с учетом отступа $m$.


Реализуем loss-функцию и модель.

In [ ]:
class ArcLoss(nn.Module):
    def __init__(self, emb_dim, num_centroids):
        super().__init__()
        self.scale = 30.0
        self.margin = 0.4
        self.eps = 1e-7

        ### YOUR CODE HERE
        self.centroids = ...

    def forward(self, f, y):
        w = self.centroids
        s = self.scale
        m = self.margin
        eps = self.eps

        ### YOUR CODE HERE
        ...

        return p, loss

In [ ]:
class ArcTrainer(BaseEmbeddingTrainer):
    def __init__(self, *, train_classes, **kwargs):
        super().__init__(**kwargs)
        self.accuracy = torchmetrics.Accuracy(
            task="multiclass",
            num_classes=train_classes,
        )

        ### YOUR CODE HERE
        self.classifier = ...

    def training_step(self, batch):
        x, y = batch

        f = self.emb_net(x)
        p, loss = self.classifier(f, y)
        accs = self.accuracy(p.argmax(dim=1), y)

        return self._log_metrics(loss, accs, "train")

Зададим провайдеры данных.

In [ ]:
sampler = data.WeightedRandomSampler(
    train_data.weights,
    len(train_data.weights),
)
arc_train_dl = data.DataLoader(
    train_data,
    BATCH_SIZE,
    sampler=sampler,
    num_workers=4,
    pin_memory=True,
)

Обучим сеть.

In [ ]:
net_arc = train_model(
    ArcTrainer(
        emb_net=EmbeddingNet(),
        train_classes=len(train_data.people_list),
    ),
    "runs/arc",
    arc_train_dl,
)

Протестируем качество k-NN.

In [ ]:
net_arc.eval()
net_arc.emb_net.to(DEVICE)
knn = train_knn(net_arc.emb_net, normalize=True)
test_knn(net_arc.emb_net, knn, normalize=True)

---